In [1]:
from utils import utils
from glob import glob
from imp import reload
from tqdm import tqdm
import codecs
import os
reload(utils)

<module 'utils.utils' from 'C:\\Users\\Administrator\\Desktop\\数据挖掘\\数据挖掘比赛\\ccf-隐私-deepshare\\ch7\\src\\utils\\utils.py'>

In [2]:
tdata_lst = glob('../data/train_data/*.txt')
symbol = ['。','!','！','?','？','﹗']

In [3]:
# 生成样本的参数
symbol = ['？','⋯','…','﹗']
max_sent_length = 250
max_input_length = 300       

## 划分训练集和验证集

In [4]:
from sklearn.model_selection import train_test_split
from glob import glob
data_lst = glob('../data/train_data/*.txt')
train_lst,val_lst = train_test_split(data_lst,test_size=0.1,random_state=0)
print('train:{}'.format(len(train_lst)))
print('val:{}'.format(len(val_lst)))

train:11935
val:1327


In [5]:
data_dir = '../data/train_label'
for data_path in tqdm(train_lst):
    file_name = os.path.basename(data_path).split('.')[0]
    label_path = file_name+'.csv'
    label_path = os.path.join(data_dir,label_path)
    output_path = '../data/train_new'
    output_file = file_name
    utils.gen_data(label_path, data_path, output_path, output_file,symbol,max_sent_length,max_input_length,bioes = False)
for data_path in tqdm(val_lst):
    file_name = os.path.basename(data_path).split('.')[0]
    label_path = file_name+'.csv'
    label_path = os.path.join(data_dir,label_path)
    output_path = '../data/val_new'
    output_file = file_name
    utils.gen_data(label_path, data_path, output_path, output_file,symbol,max_sent_length,max_input_length,bioes = False)

100%|██████████████████████████████████████████████████████████████████████████████| 1327/1327 [00:29<00:00, 44.74it/s]


## 文本数据增强
[`nlpcda`](https://github.com/425776024/nlpcda)

In [5]:
# 需要进行增强的标签
labels = [
    'position',
    'name',
    'organization',
    'company',
    'address',
    'movie',
    'game',
    'government',
    'scene',
    'book',
    'mobile',
    'email',
    'QQ',
    'vx',
]

In [6]:
# 对数据进行检查，数据要满足格式 xxx\tO\n 的形式
for filename in tqdm(glob('../data/train_new/*.txt')):
    utils.check_aug(filename)

 36%|███████████████████████████▏                                               | 4393/12145 [00:00<00:01, 4293.45it/s]

../data/train_new\1697-0-new.txt
../data/train_new\1697-1-new.txt
../data/train_new\1697-2-new.txt
../data/train_new\1697-3-new.txt


100%|██████████████████████████████████████████████████████████████████████████| 12145/12145 [00:02<00:00, 4775.28it/s]


In [7]:
from nlpcda import Ner
# ner_dir_name: 在ner数据放在ner_data目录下（里面很多.txt），BIO 标记格式
# ignore_tag_list=['O'] : 数据里面O标签的不需要管
# data_augument_tag_list=['P', 'LOC'] : 需要增强的实体
# augument_size=3 : 每条标注数据，最多新增强数量
# seed=0 : 随机种子/ 可缺省
# 原理：把目录中的实体抽出来，然后对同类实体进行随机的替换。
augument_size = 3
ner = Ner(ner_dir_name='../data/train_new/',
        ignore_tag_list=['O'],
        data_augument_tag_list=labels,
        augument_size=augument_size, seed=0)

Using TensorFlow backend.


In [10]:
for filename in tqdm(glob('../data/train_new/*.txt')):
    data_sentence_arrs, data_label_arrs = ner.augment(file_name=filename)
    if len(data_sentence_arrs) > 0:
        for aug_index in range(len(data_sentence_arrs)+1):
            output_path_ = os.path.join('../data/train_aug/','aug-{}-{}'.format(aug_index,os.path.basename(filename)))
            # 拷贝原始数据
            if aug_index == len(data_sentence_arrs):
                with codecs.open(output_path_, "w", encoding="utf-8") as w:
                    raw_file = utils.read_txt(filename)
                    for line in raw_file:
                        w.write(line)
                    w.write('{}\n'.format('END\tO'))
            # 数据增强写入
            else:
                with codecs.open(output_path_, "w", encoding="utf-8") as w:
                    for i,j in zip(data_sentence_arrs[aug_index],data_label_arrs[aug_index]):
                        line = '{}\t{}\n'.format(i,j)
                        w.write(line)
                    w.write('{}\n'.format('END\tO'))

100%|████████████████████████████████████████████████████████████████████████████| 12145/12145 [12:14<00:00, 16.54it/s]


## 数据合并成 txt

In [11]:
# 训练集合并
# 写入数据增强
w_path = "../data/train_aug.txt"
for file in os.listdir('../data/train_aug/'):
    path = os.path.join("../data/train_aug", file)
    if not file.endswith(".txt"):  
        continue
    q_list = []
    print("开始读取文件:%s" % file)
    with open(path, "r", encoding="utf-8") as f:
        line = f.readline()
        line = line.strip("\n\r")
        while line != "END\tO":
            q_list.append(line)
            line = f.readline()
            line = line.strip("\n\r")
    print("开始写入文本%s" % w_path)
    with codecs.open(w_path, "a", encoding="utf-8") as f:
        for item in q_list:
            if item.__contains__('\ufeff1'):
                print("===============")
            f.write('%s\n' % item)
        f.write('\n')

开始读取文件:aug-0-0-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-1-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-100-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-1000-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-1000-1-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10000-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10001-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10002-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10003-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10004-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10005-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10006-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10007-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10008-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10009-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-1001-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10011-0-new.txt
开始写入文本../data/trai

开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10140-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10141-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10142-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10143-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10145-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10146-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10148-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10149-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-1015-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10150-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10151-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10152-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10154-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10156-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10157-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10158-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10159-0-new.txt
开始写入文本../data/train_aug.txt
开始读取

开始读取文件:aug-0-10286-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10287-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10288-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10289-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-1029-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10290-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10291-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10292-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10293-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10294-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10295-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10297-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-103-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-1030-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10300-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10301-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10302-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10303-0-new.txt
开始写入文本

开始读取文件:aug-0-10441-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10442-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10443-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10444-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10445-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10447-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10448-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10449-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10450-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10451-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10452-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10453-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10454-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10456-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10457-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10458-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10459-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-1046-0-new.txt
开始写

开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10600-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10601-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10602-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10603-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10604-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10605-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10606-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10607-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10608-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10609-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-1061-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10610-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10611-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10612-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10613-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10614-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-0-10615-0-new.txt
开始写入文本../data/train_aug.txt
开始读取

...

开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9365-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9367-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9368-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9369-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-937-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9370-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9371-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9372-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9373-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9374-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9375-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9376-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9378-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9379-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-938-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9381-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9383-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9384-0-ne

开始读取文件:aug-3-9511-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9512-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9513-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9514-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9515-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9516-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9517-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9518-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9519-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-952-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9520-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9521-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9523-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9524-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9525-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9527-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9528-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9529-0-new.txt
开始写入文本../data/train_a

开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9667-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9668-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9669-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-967-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9670-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9671-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9672-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9673-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9674-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9675-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9676-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9677-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9678-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9679-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-968-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9680-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9681-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9683-0-ne

开始读取文件:aug-3-9818-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-982-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9820-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9822-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9823-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9824-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9825-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9826-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9827-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9828-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9829-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-983-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9830-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9831-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9832-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9833-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9834-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9835-0-new.txt
开始写入文本../data/train_au

开始读取文件:aug-3-9967-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9969-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-997-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9970-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9971-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9972-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9974-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9976-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9977-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9978-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9979-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-998-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-998-1-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9980-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9981-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9982-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9983-0-new.txt
开始写入文本../data/train_aug.txt
开始读取文件:aug-3-9984-0-new.txt
开始写入文本../data/train_aug

In [13]:
# 验证集增强（这里不做任何操作）
for file in os.listdir('../data/val_new/'):
    filename = os.path.join("../data/val_new", file)
    if not filename.endswith(".txt"):  
        continue
    output_path_ = os.path.join('../data/val_aug/','aug-{}-{}'.format(0,os.path.basename(filename)))
    with codecs.open(output_path_, "w", encoding="utf-8") as w:
        raw_file = utils.read_txt(filename)
        for line in raw_file:
            w.write(line)
        w.write('{}\n'.format('END\tO'))
# 验证集合并
w_path = "../data/val_aug.txt"
for file in os.listdir('../data/val_aug/'):
    path = os.path.join("../data/val_aug", file)
    if not file.endswith(".txt"):  
        continue
    q_list = []
    print("开始读取文件:%s" % file)
    with codecs.open(path, "r", encoding="utf-8") as f:
        line = f.readline()
        line = line.strip("\n\r")
        while line != "END\tO":
            q_list.append(line)
            line = f.readline()
            line = line.strip("\n\r")
    print("开始写入文本%s" % w_path)
    with codecs.open(w_path, "a", encoding="utf-8") as f:
        for item in q_list:
            if item.__contains__('\ufeff1'):
                print("===============")
            f.write('%s\n' % item)
        f.write('\n')
    f.close()

开始读取文件:aug-0-10010-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-10012-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-10026-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-10081-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-1009-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-10103-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-10105-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-10109-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-1011-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-10116-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-10117-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-10128-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-10135-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-1014-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-10144-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-10147-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-10153-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-10155-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-

开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11607-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11632-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11633-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11634-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11640-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11657-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11668-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-1168-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11680-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11682-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11720-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11724-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11726-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11762-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-1177-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11772-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11778-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-11790-0-new.txt
开始写入文本../dat

开始写入文本../data/val_aug.txt
开始读取文件:aug-0-12938-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-1294-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-12940-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-12949-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-12952-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-12953-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-12954-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-12962-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-13016-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-13019-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-13027-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-13028-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-13038-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-13040-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-13046-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-13075-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-13081-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-131-0-new.txt
开始写入文本../data

开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2410-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2419-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2449-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2464-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2472-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2473-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2482-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2513-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2541-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2558-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2563-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2565-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2571-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2579-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-258-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2585-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-261-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-2623-0-new.txt
开始写入文本../data/val_aug.txt
开始读取

开始读取文件:aug-0-401-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4011-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-403-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-403-1-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4040-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4048-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4060-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4067-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4074-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4100-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4119-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4138-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4140-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4142-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4143-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4146-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4151-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4177-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-4179-0-new.txt
开始写

开始读取文件:aug-0-5408-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5423-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5430-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5433-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5436-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5446-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5454-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5461-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5482-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5494-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5495-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5520-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5526-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5536-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5547-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5552-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5555-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5565-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-5572-0-new.txt


开始读取文件:aug-0-6774-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-6786-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-6794-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-6799-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-6807-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-681-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-6826-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-683-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-6846-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-6864-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-6867-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-6873-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-6876-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-6877-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-6884-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-6906-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-6911-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-692-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-6931-0-new.txt
开始写

开始读取文件:aug-0-822-1-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8222-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8223-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8242-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8244-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8250-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8258-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8259-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8260-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-828-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8286-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8288-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8319-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8321-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8338-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8341-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8348-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8349-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-8373-0-new.txt
开始

开始读取文件:aug-0-9572-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9573-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9592-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9614-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9620-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9633-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-964-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9640-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9650-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-966-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9682-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9684-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9687-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9690-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9691-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9706-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9709-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9715-0-new.txt
开始写入文本../data/val_aug.txt
开始读取文件:aug-0-9730-0-new.txt
开始